In [1]:
import numpy as np 
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import string
import re
import gc
from tqdm import tqdm  # For progress monitoring

In [2]:
# Set the display option to show the entire column value
pd.set_option('display.max_colwidth', None)

In [3]:
train_df = pd.read_csv('train.tsv', sep='\t')

In [4]:
train_df.head() 

train_id                                 name  item_condition_id  \
0         0  MLB Cincinnati Reds T Shirt Size XL                  3   
1         1     Razer BlackWidow Chroma Keyboard                  3   
2         2                       AVA-VIV Blouse                  1   
3         3                Leather Horse Statues                  1   
4         4                 24K GOLD plated rose                  1   

                                        category_name brand_name  price  \
0                                   Men/Tops/T-shirts        NaN   10.0   
1  Electronics/Computers & Tablets/Components & Parts      Razer   52.0   
2                         Women/Tops & Blouses/Blouse     Target   10.0   
3                  Home/Home Décor/Home Décor Accents        NaN   35.0   
4                             Women/Jewelry/Necklaces        NaN   44.0   

   shipping  \
0         1   
1         0   
2         1   
3         1   
4         0   

                                                                                                                                                                               item_description  
0                                                                                                                                                                            No description yet  
1  This keyboard is in great condition and works like it came out of the box. All of the ports are tested and work perfectly. The lights are customizable via the Razer Synapse app on your PC.  
2                                                                  Adorable top with a hint of lace and a key hole in the back! The pale pink is a 1X, and I also have a 3X available in white!  
3                 New with tags. Leather horses. Retail for [rm] each. Stand about a foot high. They are being sold as a pair. Any questions please ask. Free shipping. Just got out of storage  
4                                                                                                                                                     Complete with certificate of authenticity

In [5]:
train_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1482535 entries, 0 to 1482534
Data columns (total 8 columns):
 #   Column             Non-Null Count    Dtype  
---  ------             --------------    -----  
 0   train_id           1482535 non-null  int64  
 1   name               1482535 non-null  object 
 2   item_condition_id  1482535 non-null  int64  
 3   category_name      1476208 non-null  object 
 4   brand_name         849853 non-null   object 
 5   price              1482535 non-null  float64
 6   shipping           1482535 non-null  int64  
 7   item_description   1482531 non-null  object 
dtypes: float64(1), int64(3), object(4)
memory usage: 90.5+ MB


In [6]:
train_df.describe()

train_id  item_condition_id         price      shipping
count  1.482535e+06       1.482535e+06  1.482535e+06  1.482535e+06
mean   7.412670e+05       1.907380e+00  2.673752e+01  4.472744e-01
std    4.279711e+05       9.031586e-01  3.858607e+01  4.972124e-01
min    0.000000e+00       1.000000e+00  0.000000e+00  0.000000e+00
25%    3.706335e+05       1.000000e+00  1.000000e+01  0.000000e+00
50%    7.412670e+05       2.000000e+00  1.700000e+01  0.000000e+00
75%    1.111900e+06       3.000000e+00  2.900000e+01  1.000000e+00
max    1.482534e+06       5.000000e+00  2.009000e+03  1.000000e+00

In [7]:
train_df.duplicated().sum()

0

In [8]:
train_df.isnull().sum()

train_id                  0
name                      0
item_condition_id         0
category_name          6327
brand_name           632682
price                     0
shipping                  0
item_description          4
dtype: int64

# 전처리

## 이상치 처리

In [9]:
# 이상치 처리 
train_df = train_df[train_df['price'] != 0]

# 이상치 처리 확인
train_df.sort_values(by='price', ascending=False)

train_id                                      name  \
760469     760469       NEW Chanel WOC Caviar Gold Hardware   
1262245   1262245  NEW-Chanel Boy Wallet o Chain WOC Caviar   
1393600   1393600                 David Yurman Wheaton ring   
415027     415027      Chanel Classic Jumbo Single flap bag   
778940     778940                                  Mary kay   
...           ...                                       ...   
1320473   1320473                         ☆ TATTOO CHOKER ☆   
1421106   1421106                            3D ankle socks   
1320462   1320462       Blackheads removers free shipping!!   
1468628   1468628                    Hollywood Spaniel book   
145345     145345                   Woman Pampering Set (2)   

         item_condition_id                                 category_name  \
760469                   1           Women/Women's Handbags/Shoulder Bag   
1262245                  1  Women/Women's Handbags/Messenger & Crossbody   
1393600                  2                           Women/Jewelry/Rings   
415027                   3           Women/Women's Handbags/Shoulder Bag   
778940                   1                            Beauty/Makeup/Face   
...                    ...                                           ...   
1320473                  1                       Women/Jewelry/Necklaces   
1421106                  1                  Women/Athletic Apparel/Socks   
1320462                  1                         Beauty/Skin Care/Face   
1468628                  1                  Other/Books/Children's Books   
145345                   2                  Beauty/Bath & Body/Cleansers   

           brand_name   price  shipping  \
760469         Chanel  2009.0         0   
1262245        Chanel  2006.0         0   
1393600  David Yurman  2004.0         0   
415027         Chanel  2000.0         1   
778940       Mary Kay  2000.0         1   
...               ...     ...       ...   
1320473           NaN     3.0         1   
1421106           NaN     3.0         1   
1320462           NaN     3.0         1   
1468628           NaN     3.0         1   
145345            NaN     3.0         1   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             item_description  
760469                                                                                                                                                                                                                                                           New with tag, box and dustbag but no receipt. Dark purple color Cross body shoulder bag Gold hardware You must purchase and pay for two listing for the total [rm] or your purchase will be cancelled. Smoke free and Pet free home. PRICE IS FIRM thank you  
1262245                                                                                                                                                                                                                                             Brand: Chanel Style: WOC Boy Wallet on Chain Type: Crossbody shoulder bag Color: Black with ruthenium hardware Material: Caviar leather Condition: New with original packaging& copy of receipt Total price is [rm]. Must purchase and pay for both listings to be valid.  
1393600                                                                                                                                                                                                                                                                                       

## 결측치 처리

In [10]:
train_df.isnull().sum()

train_id                  0
name                      0
item_condition_id         0
category_name          6314
brand_name           632336
price                     0
shipping                  0
item_description          4
dtype: int64

### 'category_name' 결측치 삭제

In [11]:
train_df = train_df.dropna(subset=['category_name'])

### 'item_description' 유사 결측치 삭제

In [12]:
# 유사 결측치 확인 및 삭제

# Identify rows where 'item_description' contains 'no description'
no_description_mask = train_df['item_description'].str.contains('no description', case=False, na=False)

# Replace 'item_description' in those rows with NaN
train_df.loc[no_description_mask, 'item_description'] = np.nan

# Drop rows where 'item_description' is NaN
train_df = train_df.dropna(subset=['item_description'])

In [13]:
train_df.isnull().sum()

train_id                  0
name                      0
item_condition_id         0
category_name             0
brand_name           591841
price                     0
shipping                  0
item_description          0
dtype: int64

In [14]:
train_df.shape

(1393289, 8)

### 'category_name' 자르기

In [15]:
# Function to split the category_name column and ensure it always returns 3 elements
def split(category_name):
    try:
        parts = category_name.split('/')
        # Ensure the returned list is always of length 3
        return (parts + ['Null', 'Null', 'Null'])[:3]
    except AttributeError:
        return ['Null', 'Null', 'Null']

category_1 = []
category_2 = []
category_3 = []

for i in range(train_df.shape[0]):
    temp = split(train_df['category_name'].iloc[i])  # train_df['category_name'][i] 대신 train_df['category_name'].iloc[i] 사용
    category_1.append(temp[0])
    category_2.append(temp[1])
    category_3.append(temp[2])

train_df['category_1'] = category_1
train_df['category_2'] = category_2
train_df['category_3'] = category_3

print('1st Category:\n', train_df['category_1'].value_counts())
print('2nd Category:', train_df['category_2'].nunique())
print('3rd Category:', train_df['category_3'].nunique())

1st Category:
 Women                     626532
Beauty                    199877
Kids                      160906
Electronics               115110
Men                        87837
Home                       62225
Vintage & Collectibles     44108
Other                      42801
Handmade                   29769
Sports & Outdoors          24124
Name: category_1, dtype: int64
2nd Category: 113
3rd Category: 869


### 텍스트 컬럼 전처리

In [16]:
# # Text column preprocessing

# text_cols = ['name', 'brand_name', 'item_description', 'category_1', 'category_2', 'category_3']

# def preprocess_text(text):
#     if isinstance(text, str):
#         # Convert to lowercase
#         text = text.lower()
#         # Remove punctuation
#         text = text.translate(str.maketrans('', '', string.punctuation))
#         # Remove non-alphanumeric characters (except spaces and accented characters)
#         text = re.sub(r'[^\w\s\u00C0-\u017F]', '', text)
#         # Remove extra whitespace
#         text = ' '.join(text.split())
#     return text

# # Initialize tqdm
# tqdm.pandas()

# # Apply preprocessing with progress bar
# for col in text_cols:
#     print(f"Processing column: {col}")
#     train_df[col] = train_df[col].progress_apply(preprocess_text)
#     print(f"Finished processing {col}")

# print("All text preprocessing completed!")

In [17]:
# Text column preprocessing

text_cols = ['name', 'brand_name', 'item_description', 'category_1', 'category_2', 'category_3']

def preprocess_text(text):
    if isinstance(text, str):
        # Convert to lowercase
        text = text.lower()
        # Remove punctuation
        text = text.translate(str.maketrans('', '', string.punctuation))
        # Remove non-alphanumeric characters (except spaces and accented characters)
        text = re.sub(r'[^\w\s\u00C0-\u017F]', '', text)
        # Remove extra whitespace
        text = ' '.join(text.split())
    return text

chunk_size = 5000  # Adjust based on your memory capacity
num_chunks = (len(train_df) // chunk_size) + 1

# Initialize tqdm
tqdm.pandas()

# Process the data in chunks
processed_chunks = []
for i in tqdm(range(num_chunks)):
    start = i * chunk_size
    end = min((i + 1) * chunk_size, len(train_df))
    chunk = train_df.iloc[start:end].copy()

    # Apply preprocessing
    for col in text_cols:
        chunk[col] = chunk[col].progress_apply(preprocess_text)
    
    processed_chunks.append(chunk)
    
    # Explicitly delete chunk and call garbage collection to free memory
    del chunk
    gc.collect()

# Concatenate all chunks back into a single DataFrame
train_df = pd.concat(processed_chunks).reset_index(drop=True)

print("All text preprocessing completed!")

100%|██████████| 5000/5000 [00:00<00:00, 144302.76it/s]

100%|██████████| 5000/5000 [00:00<00:00, 244988.67it/s]

100%|██████████| 5000/5000 [00:00<00:00, 63498.30it/s]

100%|██████████| 5000/5000 [00:00<00:00, 176687.08it/s]

100%|██████████| 5000/5000 [00:00<00:00, 142594.53it/s]

100%|██████████| 5000/5000 [00:00<00:00, 129550.59it/s]

100%|██████████| 5000/5000 [00:00<00:00, 241693.69it/s]

100%|██████████| 5000/5000 [00:00<00:00, 64653.28it/s]

100%|██████████| 5000/5000 [00:00<00:00, 187314.28it/s]

100%|██████████| 5000/5000 [00:00<00:00, 177932.84it/s]

100%|██████████| 5000/5000 [00:00<00:00, 138254.31it/s]

100%|██████████| 5000/5000 [00:00<00:00, 260813.85it/s]

100%|██████████| 5000/5000 [00:00<00:00, 64213.60it/s]

100%|██████████| 5000/5000 [00:00<00:00, 179523.02it/s]

100%|██████████| 5000/5000 [00:00<00:00, 111985.48it/s]

100%|██████████| 5000/5000 [00:00<00:00, 136788.03it/s]

100%|██████████| 5000/5000 [00:00<00:00, 238312.73it/s]

100%|██████████| 5000/5000 [00:00<

All text preprocessing completed!


### 'brand_name' 결측치 채우기

In [18]:
# Create 'combined text' column by concatenating 'name' and 'item_description'
train_df['combined_text'] = train_df['name'] + ' ' + train_df['item_description']

# Strip leading/trailing spaces
train_df['combined_text'] = train_df['combined_text'].str.strip()

In [19]:
brand_null_head_idx = train_df[train_df['brand_name'].isnull()].head(50).index.tolist()
train_df[train_df['brand_name'].isnull()].head(50)

train_id                                      name  item_condition_id  \
2           3                     leather horse statues                  1   
3           4                      24k gold plated rose                  1   
4           5          bundled items requested for ruie                  3   
8           9    porcelain clown doll checker pants vtg                  3   
15         17         new baby ktan active baby carrier                  1   
21         23                        triple car charger                  1   
31         34          four puppy dog stuffed animal ty                  3   
32         35   black capri leggings w flowers one size                  1   
33         36                              black bag 30                  3   
39         42  lots of korean nature republic face mask                  1   
40         43            apricot beige stick foundation                  1   
41         44                      glass christmas bowl                  2   
43         46       metallic purple slime with sparkles                  1   
46         49            younique 3d fiber lash mascara                  1   
48         51          led kids shoes size 3 and size 9                  1   
49         52            hot wheelssuper tuners car set                  1   
52         55                  vintage wood jewelry lot                  3   
55         58                  new yokai watch backpack                  1   
56         59            hv900 sports bluetooth headset                  1   
57         60             14 ct diamond engagement ring                  3   
58         61    nwt lularoe os french bulldog leggings                  1   
63         66                   silver choker italy 925                  3   
66         69             iphone 66s marble design case                  1   
68         71  partners in crime necklace shipfromchina                  1   
70         73                toddler vineyard vines hat                  3   
73         76             black burgundy bikini bottoms                  1   
74         77      aura fluorite double terminated wand                  1   
75         78                               trump shirt                  3   
79         82                            mascara bundle                  2   
80         83       eyebrows essential kit medium brown                  1   
81         84       womens espresso pink coral shirt xl                  3   
82         85                         vs pink sheet set                  3   
83         86    jillian michaels bodyshred fitness dvd                  1   
89         93               crimson tide alabama tshirt                  3   
92         96       luminess air airbrush makeup system                  1   
93         97                 iphone 5s mickey ear case                  2   
94         98                                     gucci                  3   
96        100                             muscle tshirt                  3   
98        102  black boho floral embroidered maxi dress                  2   
99        103                               kids adidas                  1   
100       104                             picture frame                  2   
105       109      rose gold necklace with silver studs                  2   
106       110                   lularoe os leggings nwt                  1   
110       114          hold kesha sperry shoes ua pants                  3   
116       121                   tens 3000 lowered price                  2   
121       127                 spartina leather key fobs                  3   
122       128                           zodiac tapestry                  1   
123       130        double layer studio microphone mic                  1   
125       132                       motu skeletor dorbz                  1   
131       138   2breal girls boutique dress w adjstraps                  2   

                          

In [20]:
brand_null_tail_idx = train_df[train_df['brand_name'].isnull()].tail(50).index.tolist()
train_df[train_df['brand_name'].isnull()].tail(50)

train_id                                      name  \
1393168   1482407             slim extreme fat burner serum   
1393171   1482410             gel memory foam lumbar pillow   
1393173   1482412                      kylie jenner candy k   
1393174   1482413  lg pink hello kitty silicone baking mold   
1393176   1482415                   bellora queen duvet set   
1393178   1482417                    nwt boys shirts size 7   
1393180   1482419                    small blue lularoe joy   
1393185   1482424      marilyn monroe crochet lace 1pc swim   
1393187   1482426       dream catcher aromatherapy necklace   
1393190   1482429                     84 holo pokemon cards   
1393193   1482433          sexy cute two 2 piece shorts set   
1393194   1482434                    real technique brushes   
1393198   1482438                 curtains purple and black   
1393199   1482439               lush fun lot elf snow fairy   
1393201   1482441           freeshp heartbeat couples rings   
1393202   1482442                    ballet leotard mirella   
1393204   1482445           iphone 66s soft clear thin case   
1393206   1482448                                      cize   
1393213   1482455      little house on the prairie book set   
1393214   1482456            lularoe xxs carly stone washed   
1393216   1482458                                    bundle   
1393217   1482459                                waist belt   
1393219   1482461     lularoe web purple leggings spider os   
1393221   1482463       dallas cowboys sport utility gloves   
1393222   1482464                            asap rocky tee   
1393223   1482465               neon orange mini glass bong   
1393224   1482466                                     for v   
1393228   1482471      m bk high quality vest waist trainer   
1393229   1482472     lot of juniorsyoung womens med shirts   
1393230   1482474                    piyo workout 5 dvd set   
1393233   1482477       orangetheory heart rate monitor xss   
1393234   1482478                          large wax warmer   
1393242   1482486                         sports bra bundle   
1393249   1482493                     horizon zero dawn ps4   
1393250   1482494                  white tree long curtains   
1393255   1482501       jeffrey star velour liquid lipstick   
1393256   1482502             murano glass fish paperweight   
1393258   1482504                           herschel wallet   
1393261   1482507               grand theft auto v xbox one   
1393263   1482509                           fitbit charge 2   
1393264   1482510         2×popsockets for all phone tablet   
1393265   1482511          bebe beauty gloss icon lip gloss   
1393268   1482514                       anthropologie purse   
1393272   1482518         brooches lot of 5 assorted 1 coro   
1393276   1482522                lg k7tribute 5 hybrid case   
1393280   1482526        harry potter shirt women m girl xl   
1393281   1482527      blkwhite ribbed mock neck bodysuit m   
1393286   1482532     21 day fix containers and eating plan   
1393287   1482533                    world markets lanterns   
1393288   1482534             brand new lux de ville wallet   

         item_condition_id  \
1393168                  1   
1393171                  1   
1393173                  1   
1393174                  1   
1393176                  1   
1393178                  1   
1393180                  1   
1393185                  1   
1393187                  1   
1393190                  2   
1393193                  2   
1393194                  2   
1393198                  2   
1393199                  1   
1393201                  1   
1393202                  2   
1393204                  1   
1393206                  2   
1393213                  2   
1393214                  2   
1393216                  3   
1393217                  2   
1393219                  1   
1393221                  1   
1393222                  4   
1393223        

In [21]:
#  Count occurrences of each `brand_name` by `category_1`
brand_cat_counts_df = train_df.groupby(['brand_name', 'category_1']).size()
brand_cat_counts_df = pd.DataFrame(brand_cat_counts_df).reset_index()
brand_cat_counts_df.columns = ['brand_name', 'category_1', 'count'] 
brand_cat_counts_df = brand_cat_counts_df.sort_values(by='count', ascending=False)
brand_cat_counts_df

brand_name   category_1  count
4994              pink        women  50017
6749  victorias secret        women  37603
3887           lularoe        women  27885
4557              nike        women  23115
389              apple  electronics  16444
...                ...          ...    ...
5236             rails        women      1
5238     rainbow shops         kids      1
2568      georgia boot          men      1
2566    george foreman          men      1
7088             zyxel  electronics      1

[7089 rows x 3 columns]

In [22]:
# Filter for brands with counts > threshold 
threshold = 10
brands_df = brand_cat_counts_df[brand_cat_counts_df['count'] > threshold]
brands_df

brand_name       category_1  count
4994              pink            women  50017
6749  victorias secret            women  37603
3887           lularoe            women  27885
4557              nike            women  23115
389              apple      electronics  16444
...                ...              ...    ...
1502             coach           beauty     11
2428         frankie b            women     11
5770   shimano fishing  sports outdoors     11
2671           gorjana            women     11
4201             miche            women     11

[2046 rows x 3 columns]

In [23]:
# List of irrelevant brand names to remove
irrelevant_brands = ['all', 'm', 'ring']

# Remove rows where 'brand_name' is in the irrelevant brands list
brands_df = brands_df[~brands_df['brand_name'].isin(irrelevant_brands)]

In [24]:
# Group by 'category_1' and aggregate 'brand_name' into lists
brand_cat_dict = brands_df.groupby('category_1')['brand_name'].apply(list).to_dict()

In [25]:
# # Function to find and update the brand based on `category_1`
# def update_brand(row, brand_cat_dict):
#     if pd.isnull(row['brand_name']) or row['brand_name'] == 'all':
#         combined_text = row['combined_text']
#         category = row['category_1']
#         if category in brand_cat_dict:
#             # Check for each brand in the category
#             for brand in brand_cat_dict[category]:
#                 if re.search(r'\b' + re.escape(brand) + r'\b', combined_text):
#                     return brand
#     return row['brand_name']

# # Apply the function to each row in the DataFrame with progress bar
# tqdm.pandas(desc="Updating brands")
# train_df['brand_name'] = train_df.progress_apply(lambda row: update_brand(row, brand_cat_dict), axis=1)

In [26]:
# Sort the brand names in each category by length in descending order
for category in brand_cat_dict:
    brand_cat_dict[category] = sorted(brand_cat_dict[category], key=len, reverse=True)

# Function to find and update the brand based on `category_1`
def update_brand(row, brand_cat_dict):
    if pd.isnull(row['brand_name']) or row['brand_name'] == 'all':
        combined_text = row['combined_text']
        category = row['category_1']
        if category in brand_cat_dict:
            # Check for each brand in the category (longest first due to sorting)
            for brand in brand_cat_dict[category]:
                # Use word boundary to ensure exact match
                if re.search(r'\b' + re.escape(brand) + r'\b', combined_text):
                    return brand
    return row['brand_name']

chunk_size = 5000  # Adjust based on your memory capacity
num_chunks = (len(train_df) // chunk_size) + 1

# Initialize tqdm
tqdm.pandas()

# Process the data in chunks
processed_chunks = []
for i in tqdm(range(num_chunks)):
    start = i * chunk_size
    end = min((i + 1) * chunk_size, len(train_df))
    chunk = train_df.iloc[start:end].copy()
    
    # Apply the update_brand function to each row in the chunk
    chunk['brand_name'] = chunk.progress_apply(lambda row: update_brand(row, brand_cat_dict), axis=1)
    
    processed_chunks.append(chunk)
    
    # Explicitly delete chunk and call garbage collection to free memory
    del chunk
    gc.collect()

# Concatenate all chunks back into a single DataFrame
train_df = pd.concat(processed_chunks).reset_index(drop=True)

print("Brand updating completed!")

100%|██████████| 279/279 [2:29:39<00:00, 32.18s/it]


Brand updating completed!


In [27]:
# 'pink' > 'victorias secret' (if applicable)

# Define a function to check and update the brand name
def update_brand_pink(row):
    if row['brand_name'] == 'pink':
        if 'victorias secret' in row['combined_text'] or 'vs' in row['combined_text']:
            return 'victorias secret'
    return row['brand_name']

# Apply the function to each row in the dataframe using .loc to avoid SettingWithCopyWarning
train_df.loc[:, 'brand_name'] = train_df.apply(update_brand_pink, axis=1)

In [28]:
# 'm' > 'motorola' (if applicable)

m_mask = train_df['brand_name'] == 'm'

for idx in tqdm(train_df[m_mask].index):
    if (('motorola' in train_df.loc[idx, 'name']) or 
        ('motorola' in train_df.loc[idx, 'item_description'])):
        train_df.loc[idx, 'brand_name'] = 'motorola'

100%|██████████| 94/94 [00:00<00:00, 112.93it/s]


In [29]:
# 'galaxy' to 'samsung' (if applicable)

galaxy_mask = train_df['brand_name'] == 'galaxy'

# Steps 2 and 3: For those rows, check 'name' and 'item_description', and update if necessary
for idx in tqdm(train_df[galaxy_mask].index):
    if (('samsung' in train_df.loc[idx, 'name']) or 
        ('samsung' in train_df.loc[idx, 'item_description'])):
        train_df.loc[idx, 'brand_name'] = 'samsung'

100%|██████████| 60/60 [00:01<00:00, 54.46it/s]


In [32]:
train_df.iloc[brand_null_head_idx]

train_id                                      name  item_condition_id  \
2           3                     leather horse statues                  1   
3           4                      24k gold plated rose                  1   
4           5          bundled items requested for ruie                  3   
8           9    porcelain clown doll checker pants vtg                  3   
15         17         new baby ktan active baby carrier                  1   
21         23                        triple car charger                  1   
31         34          four puppy dog stuffed animal ty                  3   
32         35   black capri leggings w flowers one size                  1   
33         36                              black bag 30                  3   
39         42  lots of korean nature republic face mask                  1   
40         43            apricot beige stick foundation                  1   
41         44                      glass christmas bowl                  2   
43         46       metallic purple slime with sparkles                  1   
46         49            younique 3d fiber lash mascara                  1   
48         51          led kids shoes size 3 and size 9                  1   
49         52            hot wheelssuper tuners car set                  1   
52         55                  vintage wood jewelry lot                  3   
55         58                  new yokai watch backpack                  1   
56         59            hv900 sports bluetooth headset                  1   
57         60             14 ct diamond engagement ring                  3   
58         61    nwt lularoe os french bulldog leggings                  1   
63         66                   silver choker italy 925                  3   
66         69             iphone 66s marble design case                  1   
68         71  partners in crime necklace shipfromchina                  1   
70         73                toddler vineyard vines hat                  3   
73         76             black burgundy bikini bottoms                  1   
74         77      aura fluorite double terminated wand                  1   
75         78                               trump shirt                  3   
79         82                            mascara bundle                  2   
80         83       eyebrows essential kit medium brown                  1   
81         84       womens espresso pink coral shirt xl                  3   
82         85                         vs pink sheet set                  3   
83         86    jillian michaels bodyshred fitness dvd                  1   
89         93               crimson tide alabama tshirt                  3   
92         96       luminess air airbrush makeup system                  1   
93         97                 iphone 5s mickey ear case                  2   
94         98                                     gucci                  3   
96        100                             muscle tshirt                  3   
98        102  black boho floral embroidered maxi dress                  2   
99        103                               kids adidas                  1   
100       104                             picture frame                  2   
105       109      rose gold necklace with silver studs                  2   
106       110                   lularoe os leggings nwt                  1   
110       114          hold kesha sperry shoes ua pants                  3   
116       121                   tens 3000 lowered price                  2   
121       127                 spartina leather key fobs                  3   
122       128                           zodiac tapestry                  1   
123       130        double layer studio microphone mic                  1   
125       132                       motu skeletor dorbz                  1   
131       138   2breal girls boutique dress w adjstraps                  2   

                          

In [31]:
train_df.iloc[brand_null_head_idx]

train_id                                      name  item_condition_id  \
2           3                     leather horse statues                  1   
3           4                      24k gold plated rose                  1   
4           5          bundled items requested for ruie                  3   
8           9    porcelain clown doll checker pants vtg                  3   
15         17         new baby ktan active baby carrier                  1   
21         23                        triple car charger                  1   
31         34          four puppy dog stuffed animal ty                  3   
32         35   black capri leggings w flowers one size                  1   
33         36                              black bag 30                  3   
39         42  lots of korean nature republic face mask                  1   
40         43            apricot beige stick foundation                  1   
41         44                      glass christmas bowl                  2   
43         46       metallic purple slime with sparkles                  1   
46         49            younique 3d fiber lash mascara                  1   
48         51          led kids shoes size 3 and size 9                  1   
49         52            hot wheelssuper tuners car set                  1   
52         55                  vintage wood jewelry lot                  3   
55         58                  new yokai watch backpack                  1   
56         59            hv900 sports bluetooth headset                  1   
57         60             14 ct diamond engagement ring                  3   
58         61    nwt lularoe os french bulldog leggings                  1   
63         66                   silver choker italy 925                  3   
66         69             iphone 66s marble design case                  1   
68         71  partners in crime necklace shipfromchina                  1   
70         73                toddler vineyard vines hat                  3   
73         76             black burgundy bikini bottoms                  1   
74         77      aura fluorite double terminated wand                  1   
75         78                               trump shirt                  3   
79         82                            mascara bundle                  2   
80         83       eyebrows essential kit medium brown                  1   
81         84       womens espresso pink coral shirt xl                  3   
82         85                         vs pink sheet set                  3   
83         86    jillian michaels bodyshred fitness dvd                  1   
89         93               crimson tide alabama tshirt                  3   
92         96       luminess air airbrush makeup system                  1   
93         97                 iphone 5s mickey ear case                  2   
94         98                                     gucci                  3   
96        100                             muscle tshirt                  3   
98        102  black boho floral embroidered maxi dress                  2   
99        103                               kids adidas                  1   
100       104                             picture frame                  2   
105       109      rose gold necklace with silver studs                  2   
106       110                   lularoe os leggings nwt                  1   
110       114          hold kesha sperry shoes ua pants                  3   
116       121                   tens 3000 lowered price                  2   
121       127                 spartina leather key fobs                  3   
122       128                           zodiac tapestry                  1   
123       130        double layer studio microphone mic                  1   
125       132                       motu skeletor dorbz                  1   
131       138   2breal girls boutique dress w adjstraps                  2   

                          

In [33]:
train_df.isnull().sum()

train_id                  0
name                      0
item_condition_id         0
category_name             0
brand_name           399141
price                     0
shipping                  0
item_description          0
category_1                0
category_2                0
category_3                0
combined_text             0
dtype: int64

In [ ]:
# # 결측치 처리 

# train_df['brand_name'] = train_df['brand_name'].fillna(value='Unknown')

In [34]:
train_df['brand_name'].value_counts()

victorias secret    84578
lularoe             60135
nike                53004
pink                38857
apple               19723
                    ...  
olook                   1
usaf                    1
ramones                 1
arcona                  1
plugg                   1
Name: brand_name, Length: 4710, dtype: int64

In [35]:
# Save the DataFrame to a CSV file
train_df.to_csv('train_df_preprocessed.csv', index=False)

# 시각화

In [ ]:
# # 카테고리 1 빈도 시각화
# category_1_counts = train_df['category_1'].value_counts()

# plt.figure(figsize=(8, 8))
# plt.pie(category_1_counts, labels=category_1_counts.index, autopct='%1.1f%%', startangle=140)
# plt.title('Distribution of Category 1')
# plt.axis('equal')  # 원형 차트를 원형으로 유지
# plt.show()

# # 카테고리 2 빈도 시각화
# category_2_counts = train_df['category_2'].value_counts()

# plt.figure(figsize=(8, 8))
# plt.pie(category_2_counts, labels=category_2_counts.index, autopct='%1.1f%%', startangle=140)
# plt.title('Distribution of Category 2')
# plt.axis('equal')
# plt.show()

# # 카테고리 3 빈도 시각화
# category_3_counts = train_df['category_3'].value_counts()

# plt.figure(figsize=(8, 8))
# plt.pie(category_3_counts, labels=category_3_counts.index, autopct='%1.1f%%', startangle=140)
# plt.title('Distribution of Category 3')
# plt.axis('equal')
# plt.show()

In [ ]:
# # 카테고리별 평균 가격 계산
# category_1_avg_price = train_df.groupby('category_1')['price'].mean()
# category_2_avg_price = train_df.groupby('category_2')['price'].mean()
# category_3_avg_price = train_df.groupby('category_3')['price'].mean()

# # 시각화 - 막대 그래프

# # 카테고리 1 평균 가격 시각화
# plt.figure(figsize=(12, 6))
# category_1_avg_price.plot(kind='bar', color='blue')
# plt.title('Average Price by Category 1')
# plt.xlabel('Category 1')
# plt.ylabel('Average Price')
# plt.xticks(rotation=45)
# plt.show()

# # 카테고리 2 평균 가격 시각화
# plt.figure(figsize=(12, 6))
# category_2_avg_price.plot(kind='bar', color='green')
# plt.title('Average Price by Category 2')
# plt.xlabel('Category 2')
# plt.ylabel('Average Price')
# plt.xticks(rotation=90)
# plt.show()

# # 카테고리 3 평균 가격 시각화
# plt.figure(figsize=(12, 6))
# category_3_avg_price.plot(kind='bar', color='orange')
# plt.title('Average Price by Category 3')
# plt.xlabel('Category 3')
# plt.ylabel('Average Price')
# plt.xticks(rotation=90)
# plt.show()

In [ ]:
# category_counts = train_df['category_name'].value_counts()

# top_30_categories = category_counts.head(30)

# print("Top 30 categories by frequency:")
# print(top_30_categories)

In [ ]:
# category1_counts = train_df['category_1'].value_counts()

# category1_top = category1_counts

# print("Category_1 by frequency:")
# print(category1_top)

In [ ]:
# category2_counts = train_df['category_2'].value_counts()

# category2_top_30 = category2_counts.head(30)

# print("Category_2 top 30 by frequency:")
# print(category2_top_30)

In [ ]:
train_df['category_1+2'] = train_df['category_1'] + '/' + train_df['category_2']
train_df.head()

In [ ]:
# category12_counts = train_df['category_1+2'].value_counts()

# category12_top_30 = category12_counts.head(30)

# print("Category_1+2 top 30 by frequency:")
# print(category12_top_30)

In [ ]:
plt.figure(figsize=(18, 12))
sns.boxplot(data=train_df, x='category_1', y='price')
plt.show()

In [ ]:
# # 카테고리별 평균 가격 계산
# category_1_avg_price = train_df.groupby('category_1')['price'].mean()
# category_2_avg_price = train_df.groupby('category_2')['price'].mean()
# category_3_avg_price = train_df.groupby('category_3')['price'].mean()

# # 시각화 - 막대 그래프

# # 카테고리 1 평균 가격 시각화
# plt.figure(figsize=(12, 6))
# category_1_avg_price.plot(kind='bar', color='blue')
# plt.title('Average Price by Category 1')
# plt.xlabel('Category 1')
# plt.ylabel('Average Price')
# plt.xticks(rotation=45)
# plt.show()

# # 카테고리 2 평균 가격 시각화
# plt.figure(figsize=(12, 6))
# category_2_avg_price.plot(kind='bar', color='green')
# plt.title('Average Price by Category 2')
# plt.xlabel('Category 2')
# plt.ylabel('Average Price')
# plt.xticks(rotation=90)
# plt.show()

# # 카테고리 3 평균 가격 시각화
# plt.figure(figsize=(12, 6))
# category_3_avg_price.plot(kind='bar', color='orange')
# plt.title('Average Price by Category 3')
# plt.xlabel('Category 3')
# plt.ylabel('Average Price')
# plt.xticks(rotation=90)
# plt.show()

# 텍스트 처리: Bag of Words

In [ ]:
# Download NLTK resources (run this only once)
nltk.download('stopwords')

In [ ]:
def preprocess_text(text):
    # Convert text to lowercase
    text = text.lower()
    # Remove punctuation and numbers
    text = re.sub(r'[^\w\s]', '', text)
    text = re.sub(r'\d+', '', text)
    # Tokenize and remove stop words
    stop_words = set(stopwords.words('english'))
    words = text.split()
    words = [word for word in words if word not in stop_words]
    # Stem words
    stemmer = PorterStemmer()
    words = [stemmer.stem(word) for word in words]
    return ' '.join(words)

In [ ]:
def combined_bag_of_words(df, text_columns, max_features=1000):
    # Combine the specified text columns into one column for each row
    df['combined_text'] = df[text_columns].apply(lambda x: ' '.join(x.dropna().astype(str)), axis=1)
    
    # Preprocess the combined text
    df['combined_text'] = df['combined_text'].apply(preprocess_text)
    
    # Initialize CountVectorizer with max features
    vectorizer = CountVectorizer(binary=True, max_features=max_features)  # Limit vocabulary size
    X = vectorizer.fit_transform(df['combined_text'])
    
    # Convert the sparse matrix to a DataFrame
    bag_of_words_df = pd.DataFrame(X.toarray(), columns=vectorizer.get_feature_names_out())
    
    # Drop the temporary combined column
    df.drop('combined_text', axis=1, inplace=True)
    
    return bag_of_words_df

# Apply the function to the 'name' and 'item_description' columns with a max_features limit
bow_df = combined_bag_of_words(train_df, ['name', 'item_description'], max_features=1000)

print(bow_df)

In [ ]:
from wordcloud import WordCloud

# Frequency analysis
word_counts = combined_bag_of_words.sum(axis=0).sort_values(ascending=False)
print(word_counts.head(10))

# Visualization: Word Cloud
wordcloud = WordCloud(width=800, height=400, background_color='white').generate_from_frequencies(word_counts)
plt.figure(figsize=(10, 5))
plt.imshow(wordcloud, interpolation='bilinear')
plt.axis('off')
plt.show()

# Visualization: Bar Plot
top_words = word_counts.head(20)
top_words.plot(kind='bar', figsize=(10, 5))
plt.title('Top 20 Words')
plt.xlabel('Words')
plt.ylabel('Frequency')
plt.show()